In [ ]:
from google.colab import drive
drive.mount('/content/drive')

import os

os.chdir('/content/drive/My Drive/sentIA')
!ls

Mounted at /content/drive
best_model.joblib  Concatenados.csv  datatocorr.csv  report.json  target_encoder.joblib


In [ ]:
import pandas as pd

try:
  df_concatenados = pd.read_csv('Concatenados.csv')
  print("Columnas de Concatenados.csv:")
  print(df_concatenados.columns)
  print(f"Número total de columnas: {len(df_concatenados.columns)}")
except FileNotFoundError:
  pass

try:
  df_datatocorr = pd.read_csv('datatocorr.csv')
  print("\nColumnas de datatocorr.csv:")
  print(df_datatocorr.columns)
  print(f"Número total de columnas: {len(df_datatocorr.columns)}")
except FileNotFoundError:
  pass

Columnas de Concatenados.csv:
Index(['Unnamed: 0', 'ndep_proce', 'nmun_proce', 'semana', 'año', 'sexo_',
       'area_', 'pac_hos_', 'con_fin_', 'edad_', 'inten_prev', 'prob_parej',
       'enfermedad_cronica', 'prob_econo', 'muerte_fam', 'esco_educ',
       'prob_legal', 'suici_fm_a', 'maltr_fps', 'prob_labor', 'prob_famil',
       'prob_consu', 'hist_famil', 'idea_suici', 'plan_suici', 'antec_tran',
       'tran_depre', 'trast_personalidad', 'trast_bipolaridad', 'esquizofre',
       'antec_v_a', 'abuso_alco', 'ahorcamien', 'arma_corto', 'arma_fuego',
       'inmolacion', 'lanz_vacio', 'lanz_vehic', 'lanz_agua', 'intoxicaci',
       'ndep_resi'],
      dtype='object')
Número total de columnas: 41

Columnas de datatocorr.csv:
Index(['semana', 'año', 'area_', 'pac_hos_', 'con_fin_', 'edad_', 'inten_prev',
       'prob_parej', 'enfermedad_cronica', 'prob_econo',
       ...
       'ndep_resi_CARABOBO', 'ndep_resi_CAUCA', 'ndep_resi_CESAR',
       'ndep_resi_CORDOBA', 'ndep_resi_DEPTO DESC

In [ ]:
!pip install ydata-profiling

from ydata_profiling import ProfileReport

try:
  profile = ProfileReport(df_concatenados, title="Pandas Profiling Report")
  profile.to_notebook_iframe()
except NameError:
  print("df_concatenados no está definido.")

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 390.6/390.6 kB 18.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 25.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 686.1/686.1 kB 36.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.8/104.8 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 74.1 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27081 sha256=dc811db32202199697077c8152e571a1234c8aac55f6b40ee97144f4b86255fe
  Stored in directory: /root/.cache/pip/wheels/dd/91/29/a79cecb328d01739e64017b6fb9a1ab9d8cb1853098ec5966d
Successfully built htmlmin


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
json_data = profile.to_json()

# save json
with open('report.json', 'w') as f:
  f.write(json_data)

Render JSON:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
df_concatenados.columns

Index(['Unnamed: 0', 'ndep_proce', 'nmun_proce', 'semana', 'año', 'sexo_',
       'area_', 'pac_hos_', 'con_fin_', 'edad_', 'inten_prev', 'prob_parej',
       'enfermedad_cronica', 'prob_econo', 'muerte_fam', 'esco_educ',
       'prob_legal', 'suici_fm_a', 'maltr_fps', 'prob_labor', 'prob_famil',
       'prob_consu', 'hist_famil', 'idea_suici', 'plan_suici', 'antec_tran',
       'tran_depre', 'trast_personalidad', 'trast_bipolaridad', 'esquizofre',
       'antec_v_a', 'abuso_alco', 'ahorcamien', 'arma_corto', 'arma_fuego',
       'inmolacion', 'lanz_vacio', 'lanz_vehic', 'lanz_agua', 'intoxicaci',
       'ndep_resi'],
      dtype='object')

In [ ]:
import pandas as pd
import numpy as np
import xgboost as xgb
from sklearn.model_selection import train_test_split, StratifiedKFold, RandomizedSearchCV
from sklearn.metrics import classification_report, accuracy_score
from sklearn.preprocessing import LabelEncoder
from imblearn.over_sampling import SMOTE
import joblib


df_concatenados = pd.read_csv('Concatenados.csv')

df_concatenados = df_concatenados.drop(columns=['Unnamed: 0','enfermedad_cronica','ndep_proce', 'ndep_resi', 'nmun_proce', 'año', 'semana', 'pac_hos_', 'con_fin_', 'esquizofre', 'ndep_resi'])

binary_columns = [col for col in df_concatenados.columns if set(df_concatenados[col].dropna().unique()) == {1, 2}]
for col in binary_columns:
    df_concatenados[col] = df_concatenados[col].replace({1: 1, 2: 0}).astype(int)

mechanism_columns = ["ahorcamien", "arma_corto", "arma_fuego", "inmolacion",
                    "lanz_vacio", "lanz_vehic", "lanz_agua", "intoxicaci"]

df_concatenados['target_mechanism'] = df_concatenados[mechanism_columns].idxmax(axis=1)

df_concatenados = df_concatenados[df_concatenados[mechanism_columns].sum(axis=1) > 0]

def get_age_group(age):
    if age <= 6:
        return '0-6'
    elif age <= 11:
        return '7-11'
    elif age <= 17:
        return '12-17'
    elif age <= 28:
        return '18-28'
    elif age <= 59:
        return '29-59'
    else:
        return '60+'

df_concatenados['edad_group'] = df_concatenados['edad_'].apply(get_age_group)

area_dummies = pd.get_dummies(df_concatenados['area_'], prefix='area')
df_concatenados = pd.concat([df_concatenados, area_dummies], axis=1)

target_encoder = LabelEncoder()
df_concatenados['target_mechanism'] = target_encoder.fit_transform(df_concatenados['target_mechanism'])
class_names = target_encoder.classes_

encoders = {}
for col in df_concatenados.select_dtypes(include=['object']).columns:
    if col != 'target_mechanism' and col != 'edad_group':
        encoders[col] = LabelEncoder()
        df_concatenados[col] = encoders[col].fit_transform(df_concatenados[col])

columns_to_drop = mechanism_columns + ['target_mechanism', 'edad_', 'area_']
feature_columns = df_concatenados.columns.difference(columns_to_drop)

X = df_concatenados[feature_columns]
y = df_concatenados['target_mechanism']

edad_dummies = pd.get_dummies(X['edad_group'], prefix='edad')
X = X.drop('edad_group', axis=1)
X = pd.concat([X, edad_dummies], axis=1)

X_train_balanced, X_test, y_train_balanced, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)

#smote = SMOTE(random_state=42)
#X_train_balanced, y_train_balanced = smote.fit_resample(X_train, y_train)

param_dist = {
    'max_depth': [ 7],
    'learning_rate': [0.05, 0.1, 0.2],
    'n_estimators': [300],
    'gamma': [0.2]
}

xgb_clf = xgb.XGBClassifier(
    objective='multi:softmax',
    num_class=len(class_names),
    use_label_encoder=False,
    eval_metric='mlogloss'
)

cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
random_search = RandomizedSearchCV(
    xgb_clf,
    param_distributions=param_dist,
    n_iter=20,
    scoring='f1_weighted',
    cv=cv,
    random_state=42,
    n_jobs=-1
)

random_search.fit(X_train_balanced, y_train_balanced)
best_model = random_search.best_estimator_

y_pred = best_model.predict(X_test)

# resultados obtenidos
print("Best parameters found:")
print(random_search.best_params_)
print("\nClassification report:")
print(classification_report(y_test, y_pred,
                          labels=np.arange(len(class_names)),
                          target_names=class_names,
                          digits=4,
                          zero_division=0))
print(f"Accuracy: {accuracy_score(y_test, y_pred):.4f}\n")

feature_importance = pd.DataFrame({
    'feature': X.columns,
    'importance': best_model.feature_importances_
})
feature_importance = feature_importance.sort_values('importance', ascending=False)

print("\nTop 10 Most Important Features:")
print(feature_importance.head(10))

joblib.dump(best_model, 'best_model.joblib')
joblib.dump(target_encoder, 'target_encoder.joblib')


<ipython-input-21-715a3be94d69>:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_concatenados['edad_group'] = df_concatenados['edad_'].apply(get_age_group)
/usr/local/lib/python3.10/dist-packages/sklearn/model_selection/_search.py:320: UserWarning: The total space of parameters 3 is smaller than n_iter=20. Running 3 iterations. For exhaustive searches, use GridSearchCV.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:158: UserWarning: [01:18:56] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)


Best parameters found:
{'n_estimators': 300, 'max_depth': 7, 'learning_rate': 0.2, 'gamma': 0.2}

Classification report:
              precision    recall  f1-score   support

  ahorcamien     0.0000    0.0000    0.0000        78
  arma_corto     0.4444    0.1758    0.2520       273
  arma_fuego     0.0000    0.0000    0.0000         4
  inmolacion     0.0000    0.0000    0.0000         2
  intoxicaci     0.6940    0.9514    0.8026       906
   lanz_agua     0.0000    0.0000    0.0000         1
  lanz_vacio     0.1667    0.0128    0.0238        78
  lanz_vehic     0.0000    0.0000    0.0000        18

    accuracy                         0.6699      1360
   macro avg     0.1631    0.1425    0.1348      1360
weighted avg     0.5611    0.6699    0.5866      1360

Accuracy: 0.6699


Top 10 Most Important Features:
       feature  importance
13  prob_consu    0.110832
17  prob_legal    0.056898
29   edad_7-11    0.055748
19       sexo_    0.055295
1   antec_tran    0.053818
9   inten_prev 

['target_encoder.joblib']

In [ ]:
np.unique(df_concatenados['target_mechanism'], return_counts=True)

(array([0, 1, 2, 3, 4, 5, 6, 7]),
 array([ 390, 1366,   17,   11, 4528,    7,  391,   90]))

In [ ]:
np.unique(y_pred)

array([0, 1, 4, 6], dtype=int32)

too much desbalance :u

In [ ]:
len(['Unnamed: 0', 'abuso_alco', 'antec_tran', 'antec_v_a', 'area_1',
       'area_2', 'area_3', 'edad_group', 'enfermedad_cronica', 'esco_educ',
       'hist_famil', 'idea_suici', 'inten_prev', 'maltr_fps', 'muerte_fam',
       'plan_suici', 'prob_consu', 'prob_econo', 'prob_famil', 'prob_labor',
       'prob_legal', 'prob_parej', 'sexo_', 'suici_fm_a', 'tran_depre',
       'trast_bipolaridad', 'trast_personalidad'])

27

In [ ]:
feature_columns

Index(['Unnamed: 0', 'abuso_alco', 'antec_tran', 'antec_v_a', 'area_1',
       'area_2', 'area_3', 'edad_group', 'enfermedad_cronica', 'esco_educ',
       'hist_famil', 'idea_suici', 'inten_prev', 'maltr_fps', 'muerte_fam',
       'plan_suici', 'prob_consu', 'prob_econo', 'prob_famil', 'prob_labor',
       'prob_legal', 'prob_parej', 'sexo_', 'suici_fm_a', 'tran_depre',
       'trast_bipolaridad', 'trast_personalidad'],
      dtype='object')

In [ ]:
X.describe()

In [ ]:
len(['sexo_',
       'area_',
        'edad_', 'inten_prev', 'prob_parej',
       'enfermedad_cronica', 'prob_econo', 'muerte_fam', 'esco_educ',
       'prob_legal', 'suici_fm_a', 'maltr_fps', 'prob_labor', 'prob_famil',
       'prob_consu', 'hist_famil', 'idea_suici', 'plan_suici', 'antec_tran',
       'tran_depre', 'trast_personalidad', 'trast_bipolaridad',
       'antec_v_a', 'abuso_alco'])

In [ ]:
import pandas as pd
import joblib
import json

def predict_mechanism(json_data):
    # Load the model and encoder
    model = joblib.load('best_model.joblib')
    target_encoder = joblib.load('target_encoder.joblib')

    # Convert JSON string to dictionary if string is provided
    if isinstance(json_data, str):
        data = json.loads(json_data)
    else:
        data = json_data

    # Create DataFrame with single row
    df = pd.DataFrame([data])

    # Convert binary values (1,2) to (1,0)
    binary_columns = [col for col in df.columns if col != 'sexo_' and col != 'area_'
                     and col != 'edad_' and col != 'prob_consu']
    for col in binary_columns:
        df[col] = df[col].replace({1: 1, 2: 0}).astype(int)

    # Create age group
    def get_age_group(age):
        if age <= 6: return '0-6'
        elif age <= 11: return '7-11'
        elif age <= 17: return '12-17'
        elif age <= 28: return '18-28'
        elif age <= 59: return '29-59'
        else: return '60+'

    df['edad_group'] = df['edad_'].apply(get_age_group)
    df = df.drop('edad_', axis=1)

    # Create dummy variables for area with all possible categories
    area_categories = [1, 2, 3]  # All possible area categories
    for area in area_categories:
        df[f'area_{area}'] = (df['area_'] == area).astype(int)
    df = df.drop('area_', axis=1)

    # Create dummy variables for age group with all possible categories
    age_categories = ['0-6', '7-11', '12-17', '18-28', '29-59', '60+']
    for age in age_categories:
        df[f'edad_{age}'] = (df['edad_group'] == age).astype(int)
    df = df.drop('edad_group', axis=1)

    # Convert sex to numeric (assuming 'M'=1, 'F'=0)
    df['sexo_'] = (df['sexo_'] == 'M').astype(int)

    # Drop unnecessary columns
    df = df.drop('enfermedad_cronica', axis=1, errors='ignore')

    # Ensure columns are in the correct order
    expected_columns = ['abuso_alco', 'antec_tran', 'antec_v_a', 'area_1', 'area_2', 'area_3',
                       'esco_educ', 'hist_famil', 'idea_suici', 'inten_prev', 'maltr_fps',
                       'muerte_fam', 'plan_suici', 'prob_consu', 'prob_econo', 'prob_famil',
                       'prob_labor', 'prob_legal', 'prob_parej', 'sexo_', 'suici_fm_a',
                       'tran_depre', 'trast_bipolaridad', 'trast_personalidad', 'edad_0-6',
                       'edad_12-17', 'edad_18-28', 'edad_29-59', 'edad_60+', 'edad_7-11']

    # Reorder columns to match training data
    df = df[expected_columns]

    # Make prediction
    prediction = model.predict(df)
    print(prediction)
    mechanism = target_encoder.inverse_transform([prediction])[0]

    return mechanism

# Example usage
json_input = '''{"plan_suici":"1","antec_tran":"2","tran_depre":"2","trast_personalidad":"2",
              "trast_bipolaridad":"1","antec_v_a":"2","abuso_alco":"2","inten_prev":"2",
              "prob_parej":"1","enfermedad_cronica":"2","prob_econo":"2","muerte_fam":"2",
              "esco_educ":"1","prob_legal":"1","suici_fm_a":"2","maltr_fps":"2","prob_labor":"2",
              "prob_famil":"1","hist_famil":"1","idea_suici":"2","sexo_":"F","edad_":17,"area_":1,
              "prob_consu":1}'''

predicted_mechanism = predict_mechanism(json_input)
print(f"Predicted mechanism: {predicted_mechanism}")

[1]
Predicted mechanism: arma_corto


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_label.py:153: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
